In [56]:
import numpy as np
import pandas as pd
from sklearn.model_selection import train_test_split
from sklearn.linear_model import LinearRegression
from sklearn.metrics import mean_squared_error, mean_absolute_error
from sklearn import preprocessing
import statsmodels.api as sm
import plotly.figure_factory as ff
import plotly.express as px

In [57]:
import os
print(os.listdir("/kaggle/input/calcofi"))

['bottle.csv', 'cast.csv']


In [58]:
data=pd.read_csv("/kaggle/input/calcofi/bottle.csv", nrows=100000)
data=data[data["T_degC"].notnull()]
data=data[data["Depthm"].notnull()]
data=data[data["Salnty"].notnull()]
data=data[["Depthm","T_degC","STheta","R_SVA","Salnty"]]
#STheta: Density anomaly calculated with the potential temperature, salinity, and at 0 decibars pressure
#Density depends on heat content and salinity
#https://calcofi.com/index.php?option=com_content&view=category&id=29&Itemid=505&limitstart=10

In [59]:
data=data.sample(frac=0.2, replace=True).reset_index(drop=True)#.head(5000)

In [60]:
data.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 14722 entries, 0 to 14721
Data columns (total 5 columns):
 #   Column  Non-Null Count  Dtype  
---  ------  --------------  -----  
 0   Depthm  14722 non-null  int64  
 1   T_degC  14722 non-null  float64
 2   STheta  14722 non-null  float64
 3   R_SVA   14583 non-null  float64
 4   Salnty  14722 non-null  float64
dtypes: float64(4), int64(1)
memory usage: 575.2 KB


In [61]:
data.head(5)

Depthm  T_degC  STheta  R_SVA  Salnty
0       0   13.71  25.096  285.6  33.510
1     900    4.21  27.348   81.0  34.467
2      97    9.58  25.243  273.6  32.720
3     400    6.01  26.844  125.2  34.099
4      20   11.47  25.224  274.0  33.114

In [62]:
fig = ff.create_distplot([data["Salnty"]], ["Salnty"])
fig.show()

In [63]:
fig = ff.create_distplot([data["T_degC"]], ["T_degC"])
fig.show()

In [64]:
fig = ff.create_distplot([data["Depthm"]], ["Depthm"])
fig.show()

In [65]:
fig = px.histogram(data, x="T_degC", y="Salnty",
                   hover_data=data.columns)
fig.show()

In [66]:
fig = px.histogram(data, x="Depthm", y="Salnty",
                   hover_data=data.columns)
fig.show()

In [67]:
data_hot=data[(data.T_degC >= 0)]
fig = px.scatter(data_hot, x="Depthm", y="Salnty", trendline="ols")
fig.show()

# Salinity= B0+B1*T_degC+B2*Depthm

In [68]:
fig = px.scatter_3d(data, x='Depthm', y='T_degC', z='Salnty',color='T_degC',size='Salnty')           
fig.update_traces(marker_size = 2)
fig.show()

In [69]:
model = LinearRegression()
X=data_hot[["Depthm", "T_degC"]]
Y=data_hot[["Salnty"]]

In [70]:
X_train, X_test, Y_train, Y_test = train_test_split(
    X, Y, test_size=0.3, random_state=128)


In [71]:
model.fit(X_train,Y_train)

LinearRegression()

In [72]:
predictions = model.predict(X_test)

In [73]:
print(f"Accuracy {round(model.score(X_train,Y_train)*100,3)} %")

Accuracy 51.621 %


In [74]:
print(
  'Mean Squared Error : ', mean_squared_error(Y_test, predictions))
print(
  'Mean Absolute Error : ', mean_absolute_error(Y_test, predictions))

Mean Squared Error :  0.13149787897052423
Mean Absolute Error :  0.25875174602749307


In [75]:
fig = px.scatter(x=np.squeeze(predictions), y=np.squeeze(Y_test), trendline="ols", labels=dict(x='Predicted Value', y='True Value'))#must be 1D array so i used squeeze to remove (x,1) dimension
fig.add_hline(y=model.intercept_[0], line_width=2, line_color='Green', name="lol")
fig.update(layout_yaxis_range = [30,37])
fig.show()

In [76]:
function=f"Salnty = {model.intercept_[0]} + {model.coef_[0][0]} * Depthm + {model.coef_[0][1]} * T_degC"
print(function)


Salnty = 33.79012094652334 + 0.0007919067200365242 * Depthm + -0.020356359449805832 * T_degC


In [77]:
fig = px.scatter(data_hot, x="Depthm", y="Salnty", trendline="ols")
#fig.add_shape(type="line",
#              x0=0, 
#              y0=model.intercept_[0]+0*model.coef_[0][0], 
#              x1=100, 
#              y1=model.intercept_[0]+100*model.coef_[0][0])
fig.show()

# STATMODELS

In [78]:
X_train = sm.add_constant(X_train)
X_test = sm.add_constant(X_test)
smodel = sm.OLS(Y_train, X_train)
results = smodel.fit()
print(results.summary())

                            OLS Regression Results                            
Dep. Variable:                 Salnty   R-squared:                       0.516
Model:                            OLS   Adj. R-squared:                  0.516
Method:                 Least Squares   F-statistic:                     5496.
Date:                Wed, 04 Jan 2023   Prob (F-statistic):               0.00
Time:                        06:28:59   Log-Likelihood:                -4325.9
No. Observations:               10305   AIC:                             8658.
Df Residuals:                   10302   BIC:                             8679.
Df Model:                           2                                         
Covariance Type:            nonrobust                                         
                 coef    std err          t      P>|t|      [0.025      0.975]
------------------------------------------------------------------------------
const         33.7901      0.016   2065.017      0.0

In [79]:
print(f"R Squared: {results.rsquared}\n")

print(f"Adjusted R Squared: {results.rsquared_adj}\n")

print(f"Estimators:\n{results.params}")

R Squared: 0.5162103242184808

Adjusted R Squared: 0.5161164027127961

Estimators:
const     33.790121
Depthm     0.000792
T_degC    -0.020356
dtype: float64


In [80]:
#from statsmodels.stats.outliers_influence import OLSInfluence
#influence = OLSInfluence(results)
#influence.summary_frame()

In [81]:
white_test=sm.stats.diagnostic.het_white(results.resid,results.model.exog)
labels = ['Test Statistic', 'Test Statistic p-value', 'F-Statistic', 'F-Test p-value']
w_sonuclar=zip(labels, white_test)
print(*w_sonuclar)

('Test Statistic', 2889.3470517994815) ('Test Statistic p-value', 0.0) ('F-Statistic', 802.5560390795736) ('F-Test p-value', 0.0)


In [82]:
fig = ff.create_distplot([results.resid], ["Residuals"])
fig.show()


# Sonuclar

<div><ol><li><font color="Green" ><b>Adj R2</b> </font>: 1-[SSResidual/(n-K)/SStotal/(n-1)]. Corrected goodness-of-fit (model accuracy) 1 iyi 0 kotu. 0.2 cikti. Ama sadece 2 degiskenle 0.2 gercek veri icin iyi bir sonuc.</li><br>
    <img src="https://www.graphpad.com/guides/prism/latest/curve-fitting/images/reg_adjustedr2equation.png" width="500"/>
<li>Durbinwatson Test: 0-2-4 araliklari var. Residuals icin test yapilir, 2 ise otokorelasyon yok, 0-2 ise pozitif 2-4 ise negatif korelasyon var. Bizdeki deger 2.018 yani otokorelasyon yok.  </li>  <br>
    <img src="https://itfeature.com/wp-content/uploads/2020/05/DW-d.png" width="500"/>
<li>t-test : Null hipotezde u1=u2 mean degerlerinin esitligini kontrol eder, degisken anlamli mi onu test ediyor. Tum degerlerimiz anlamli.  </li><br>
    <img src="https://analystprep.com/study-notes/wp-content/uploads/2018/09/hypothesis-test-under-multiple-regression.png" width="500"/>
<li> F-test: t-test gibi ancak varyanslara bakiyor, F score hesabinda R2 kullanilir. Regresyonumuzun F testi de anlamli.</li><br>
    <img src="https://timeseriesreasoning.files.wordpress.com/2021/06/fd8fe-195ftcbbwg1cttrq-jts9ha.png" width="500"/>
    
<li>Jarque-Bera test: Normallik testi, residuals normal mi dagiliyor onu test eder. Skew ve Kurtosis(dependent variable) kullanilarak hespalanir.Normal dagilimin skewness degeri 0dir, simetrik dagilimlarin da sifira yakin cikar. Dagilim sag tarafta fazlaysa pozitif soldaysa negatif skewness degeri cikar.Normal dagilimda Kurtosis 3 cikar. 3ten buyuk ise heavy-tailed", dusuk ise light-tailed" dagilimdir.(tailin dikey kalinligi)</li><br>
    <img src="https://timeseriesreasoning.files.wordpress.com/2021/06/df191-1qt3oh9dfl8zxjrlx49mzhg.png" width="500"/>
<li>Omnibus test: Bir veri setinde açıklanan varyansın genel olarak açıklanamayan varyanstan önemli ölçüde büyük olup olmadığını test eder.</li>
    <img src="https://www.graphpad.com/guides/prism/latest/curve-fitting/images/reg_adjustedr2equation.png" width="500"/>
    <li>White`s Heteroscedasticity test: Bir veri setinde açıklanan varyansın genel olarak açıklanamayan varyanstan önemli ölçüde büyük olup olmadığını test eder.</li>
</ol></div>



In [83]:
labels = ['Jarque-Bera', 'Chi^2 two-tail prob.', 'Skew', 'Kurtosis']
jb_test = sm.stats.stattools.jarque_bera(results.resid)
jb_sonuclar=zip(labels, jb_test)
print(*jb_sonuclar)

('Jarque-Bera', 2660.019853615497) ('Chi^2 two-tail prob.', 0.0) ('Skew', -0.44975273358250384) ('Kurtosis', 5.320772952938035)


In [84]:
# t test u1=u2
r = np.zeros_like(results.params)
r[1:]=[1,-1] # Tdeg vs depth 
results.t_test(r)

<class 'statsmodels.stats.contrast.ContrastResults'>
                             Test for Constraints                             
                 coef    std err          t      P>|t|      [0.025      0.975]
------------------------------------------------------------------------------
c0             0.0211      0.001     17.003      0.000       0.019       0.024

In [85]:
# F-test
results.fvalue
results.f_test(np.array([0,-1,1]))    # Tdeg vs depth 

<class 'statsmodels.stats.contrast.ContrastResults'>
<F test: F=289.1029501421602, p=5.790785113750434e-64, df_denom=1.03e+04, df_num=1>

In [86]:
#  multicollinearity test
corr = np.corrcoef(X_train[["Depthm", "T_degC"]], rowvar=0)
w, v = np.linalg.eig(corr) #eigenvalues and eigenvectors, eigenvalue->0 = covariance

print(f"Korelasyon matrisi:\n{corr}\n")
print(f"Ozdegerler:\n{w}\n")
print(f"Ozvektorler:\n{v[:,0]}\n'")
print("Korelasyon yok")

Korelasyon matrisi:
[[ 1.        -0.7695849]
 [-0.7695849  1.       ]]

Ozdegerler:
[1.7695849 0.2304151]

Ozvektorler:
[ 0.70710678 -0.70710678]
'
Korelasyon yok


# Polynomial Regression

In [87]:
from sklearn.preprocessing import PolynomialFeatures
polynomial_features= PolynomialFeatures(degree=3)
polynomial_features_t= PolynomialFeatures(degree=3)
xp = polynomial_features.fit_transform(X_train)
xt = polynomial_features_t.fit_transform(X_test)
feature_list=enumerate(polynomial_features.get_feature_names_out(X_train.columns))
print(*feature_list)

(0, '1') (1, 'const') (2, 'Depthm') (3, 'T_degC') (4, 'const^2') (5, 'const Depthm') (6, 'const T_degC') (7, 'Depthm^2') (8, 'Depthm T_degC') (9, 'T_degC^2') (10, 'const^3') (11, 'const^2 Depthm') (12, 'const^2 T_degC') (13, 'const Depthm^2') (14, 'const Depthm T_degC') (15, 'const T_degC^2') (16, 'Depthm^3') (17, 'Depthm^2 T_degC') (18, 'Depthm T_degC^2') (19, 'T_degC^3')


In [88]:
pmodel = sm.OLS(Y_train, xp)
presult=pmodel.fit()

In [89]:
print(presult.summary())

                            OLS Regression Results                            
Dep. Variable:                 Salnty   R-squared:                       0.758
Model:                            OLS   Adj. R-squared:                  0.758
Method:                 Least Squares   F-statistic:                     3589.
Date:                Wed, 04 Jan 2023   Prob (F-statistic):               0.00
Time:                        06:28:59   Log-Likelihood:                -749.52
No. Observations:               10305   AIC:                             1519.
Df Residuals:                   10295   BIC:                             1591.
Df Model:                           9                                         
Covariance Type:            nonrobust                                         
                 coef    std err          t      P>|t|      [0.025      0.975]
------------------------------------------------------------------------------
const          8.4487      0.037    226.515      0.0

In [90]:
predictions = presult.predict(xt)
print(
  'Mean Squared Error : ', mean_squared_error(Y_test, predictions))
print(
  'Mean Absolute Error : ', mean_absolute_error(Y_test, predictions))

Mean Squared Error :  0.06919359778215178
Mean Absolute Error :  0.18263954388117554


In [91]:
fig = ff.create_distplot([presult.resid], ["Residuals"])
fig.show()

In [92]:
fig = ff.create_distplot([results.resid], ["Residuals"])
fig.show()

In [93]:
masked_cor=np.ma.masked_invalid(xp[:,1:])
pcorr = np.ma.corrcoef(masked_cor, rowvar=0)
pw, pv = np.linalg.eig(pcorr) #eigenvalues and eigenvectors, eigenvalue 0a yakinsa collinearity var

print(f"Korelasyon matrisi:\n{pcorr}\n")
print(f"Ozdegerler:\n{pw}\n")
print(f"Ozvektorler:\n{pv[:,0]}\n'")
print("Korelasyon var")

Korelasyon matrisi:
[[-- -- -- -- -- -- -- -- -- -- -- -- -- -- -- -- -- -- --]
 [-- 1.0 -0.7695849025892952 -- 1.0 -0.7695849025892952
  0.8694439870674762 0.8940175777311153 -0.631761977429661 -- 1.0
  -0.7695849025892952 0.8694439870674762 0.8940175777311153
  -0.631761977429661 0.6347742309107811 0.984761647622097
  0.3539608713079306 -0.5084430578752516]
 [-- -0.7695849025892952 1.0 -- -0.7695849025892952 1.0
  -0.5009156830176964 -0.8281741146040951 0.9717888999335361 --
  -0.7695849025892952 1.0 -0.5009156830176964 -0.8281741146040951
  0.9717888999335361 -0.2777086961594569 -0.6844838327464614
  -0.39127635410302325 0.9031864507690767]
 [-- -- -- -- -- -- -- -- -- -- -- -- -- -- -- -- -- -- --]
 [-- 1.0 -0.7695849025892952 -- 1.0 -0.7695849025892952
  0.8694439870674762 0.8940175777311153 -0.631761977429661 -- 1.0
  -0.7695849025892952 0.8694439870674762 0.8940175777311153
  -0.631761977429661 0.6347742309107811 0.984761647622097
  0.3539608713079306 -0.5084430578752516]
 [-- -

In [94]:
#pcorr[np.isnan(pcorr)]=0
fig = px.imshow(pcorr, text_auto=True, title="Correlation Matrix")
fig.show()

In [95]:
model2 = LinearRegression()
X=data_hot.copy()
X=X[["Depthm","T_degC","STheta","R_SVA","Salnty"]]
X=X.dropna()
Y=X[["Salnty"]]
X=X.drop("Salnty", axis=1)
X_train, X_test, Y_train, Y_test = train_test_split(
    X, Y, test_size=0.3, random_state=128)#random state -> random seed, ayni randomizeri uretmeye yarar


In [96]:
fig = px.scatter(data_hot, x="STheta", y="Salnty", trendline="ols")
fig.show()

In [97]:
fig = px.scatter(data_hot, x="R_SVA", y="Salnty", trendline="ols")
fig.show()

In [98]:
X_train

Depthm  T_degC  STheta  R_SVA
12514     300    7.11  26.639  143.9
10297     150   11.12  26.206  183.8
12436      30   12.24  24.961  299.2
14047      98    9.46  26.005  201.2
5388      100    8.44  25.541  245.1
...       ...     ...     ...    ...
2081      125    8.25  26.303  173.2
2413      102   11.59  25.395  259.7
13928      85   10.90  25.830  217.8
7321      148    7.72  26.202  183.0
11577      20   18.97  23.877  402.5

[10208 rows x 4 columns]

In [99]:
#X_train = sm.add_constant(X_train)
smodel = sm.OLS(Y_train, X_train)
results=smodel.fit()
print(results.summary())

                                 OLS Regression Results                                
Dep. Variable:                 Salnty   R-squared (uncentered):                   1.000
Model:                            OLS   Adj. R-squared (uncentered):              1.000
Method:                 Least Squares   F-statistic:                          3.410e+08
Date:                Wed, 04 Jan 2023   Prob (F-statistic):                        0.00
Time:                        06:29:00   Log-Likelihood:                          9793.5
No. Observations:               10208   AIC:                                 -1.958e+04
Df Residuals:                   10204   BIC:                                 -1.955e+04
Df Model:                           4                                                  
Covariance Type:            nonrobust                                                  
                 coef    std err          t      P>|t|      [0.025      0.975]
-----------------------------------------

In [100]:
predictions = results.predict(X_test)
print(
  'Mean Squared Error : ', mean_squared_error(Y_test, predictions))
print(
  'Mean Absolute Error : ', mean_absolute_error(Y_test, predictions))

Mean Squared Error :  0.008597010822831432
Mean Absolute Error :  0.06410411583393721


In [101]:
fig = px.scatter(x=np.squeeze(predictions), y=np.squeeze(Y_test), trendline="ols", labels=dict(x='Predicted Value', y='True Value'))#must be 1D array so i used squeeze to remove (x,1) dimension
fig.add_hline(y=model.intercept_[0], line_width=2, line_color='Green', name="lol")
#fig.update(layout_yaxis_range = [30,37])
fig.show()

Density anomaly is directly related with salinity and temperature. So R squared resulted 1.